In [0]:
# Importing Libraries
from pyspark.sql import SparkSession
import pandas as pd
from pyspark.sql.functions import round, year, sum
from pyspark.sql.functions import substring

In [0]:
# start the sparksession
spark = SparkSession.builder \
                .appName("Ecommerce_data_analysis") \
                    .getOrCreate()

In [0]:
# creating the dataframe for product, sales and Order
product_df = spark.read.format("csv") \
                        .option("header", True) \
                            .option("sep", ",") \
                                .load("/FileStore/tables/Product.csv")

order_df = spark.read.json("/FileStore/tables/Order.json", multiLine=True)

customer_df = spark.read.format("com.crealytics.spark.excel") \
                        .option("header", "true") \
                        .option("inferSchema", "true") \
                        .option("dataAddress", "'Worksheet'!A2:K794") \
                        .load("dbfs://FileStore/tables/Customer.xls")

---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-4244936966541354>:9
      2 product_df = spark.read.format("csv") \
      3                         .option("header", True) \
      4                             .option("sep", ",") \
      5                                 .load("/FileStore/tables/Product.csv")
      7 order_df = spark.read.json("/FileStore/tables/Order.json", multiLine=True)
----> 9 customer_df = spark.read.format("com.crealytics.spark.excel") \
     10                         .option("header", "true") \
     11                         .option("inferSchema", "true") \
     12                         .option("dataAddress", "'Worksheet'!A2:K794") \
     13                         .load("dbfs://FileStore/tables/Customer.xls")

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start

In [0]:
pandasDF = pd.read_excel("/dbfs/FileStore/tables/Customer.xlsx") 

---------------------------------------------------------------------------
FileNotFoundError                         Traceback (most recent call last)
File <command-4244936966541357>:1
----> 1 pandasDF = pd.read_excel(r"/FileStore/tables/Customer.xlsx")

File /databricks/python/lib/python3.9/site-packages/pandas/util/_decorators.py:311, in deprecate_nonkeyword_arguments.<locals>.decorate.<locals>.wrapper(*args, **kwargs)
    305 if len(args) > num_allow_args:
    306     warnings.warn(
    307         msg.format(arguments=arguments),
    308         FutureWarning,
    309         stacklevel=stacklevel,
    310     )
--> 311 return func(*args, **kwargs)

File /databricks/python/lib/python3.9/site-packages/pandas/io/excel/_base.py:457, in read_excel(io, sheet_name, header, names, index_col, usecols, squeeze, dtype, engine, converters, true_values, false_values, skiprows, nrows, na_values, keep_default_na, na_filter, verbose, parse_dates, date_parser, thousands, decimal, comment, skipfoo

In [0]:
product_df.show(5)

+---------------+---------------+------------+--------------------+--------+-----------------+
|     Product ID|       Category|Sub-Category|        Product Name|   State|Price per product|
+---------------+---------------+------------+--------------------+--------+-----------------+
|FUR-CH-10002961|      Furniture|      Chairs|Leather Task Chai...|New York|           81.882|
|TEC-AC-10004659|     Technology| Accessories|Imation Secure+ H...|Oklahoma|            72.99|
|OFF-BI-10002824|Office Supplies|     Binders|Recycled Easel Ri...|Colorado|             4.25|
|OFF-PA-10003349|Office Supplies|       Paper|          Xerox 1957| Florida|            5.184|
|TEC-AC-10003023|     Technology| Accessories|Logitech G105 Gam...|    Ohio|           47.496|
+---------------+---------------+------------+--------------------+--------+-----------------+
only showing top 5 rows



In [0]:
order_df.show(5)

+-----------+--------+----------+--------------+-------+---------------+-------+--------+------+---------+--------------+
|Customer ID|Discount|Order Date|      Order ID|  Price|     Product ID| Profit|Quantity|Row ID|Ship Date|     Ship Mode|
+-----------+--------+----------+--------------+-------+---------------+-------+--------+------+---------+--------------+
|   JK-15370|     0.3| 21/8/2016|CA-2016-122581|573.174|FUR-CH-10002961| 63.686|       7|     1|25/8/2016|Standard Class|
|   BD-11320|     0.0| 23/9/2017|CA-2017-117485| 291.96|TEC-AC-10004659|102.186|       4|     2|29/9/2017|Standard Class|
|   LB-16795|     0.7| 6/10/2016|US-2016-157490|     17|OFF-BI-10002824| -14.92|       4|     3|7/10/2016|   First Class|
|   KB-16315|     0.2|  2/7/2015|CA-2015-111703| 15.552|OFF-PA-10003349| 5.6376|       3|     4| 9/7/2015|Standard Class|
|   DO-13435|     0.2| 3/10/2014|CA-2014-108903|142.488|TEC-AC-10003023|   -3.0|       3|     5|3/10/2014|      Same Day|
+-----------+--------+--

In [0]:
# Data enrichment
# Profit rounded to 2 decimal places
# Create an enriched table which has
# order information 
# Profit rounded to 2 decimal places
# Customer name and country
# Product category and sub category
# Create an aggregate table that shows profit by 
# Year
# Product Category
# Product Sub Category
# Customer

order_df = order_df.withColumn('Profit', round(order_df['Profit'], 2))


---------------------------------------------------------------------------
AttributeError                            Traceback (most recent call last)
File <command-4244936966541361>:1
----> 1 order_df = order_df.withColumnrenamed('Profit', round(order_df['Profit'], 2))

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databricks/spark/python/pyspark/sql/dataframe.py:2964, in DataFrame.__getattr__(self, name)
   2934 """Returns the :class:`Column` denoted by ``name``.
   2935 
   2936 .. versionadded:: 1.3.0
   (...)
   2961 +---+
   2962 """
   2963 if name not in self.columns:
-> 2964     raise AttributeError(
   2965         "'%s' object has no attribute '%s

In [0]:
order_df.show(5)

+-----------+--------+----------+--------------+-------+---------------+------+--------+------+---------+--------------+
|Customer ID|Discount|Order Date|      Order ID|  Price|     Product ID|Profit|Quantity|Row ID|Ship Date|     Ship Mode|
+-----------+--------+----------+--------------+-------+---------------+------+--------+------+---------+--------------+
|   JK-15370|     0.3| 21/8/2016|CA-2016-122581|573.174|FUR-CH-10002961| 63.69|       7|     1|25/8/2016|Standard Class|
|   BD-11320|     0.0| 23/9/2017|CA-2017-117485| 291.96|TEC-AC-10004659|102.19|       4|     2|29/9/2017|Standard Class|
|   LB-16795|     0.7| 6/10/2016|US-2016-157490|     17|OFF-BI-10002824|-14.92|       4|     3|7/10/2016|   First Class|
|   KB-16315|     0.2|  2/7/2015|CA-2015-111703| 15.552|OFF-PA-10003349|  5.64|       3|     4| 9/7/2015|Standard Class|
|   DO-13435|     0.2| 3/10/2014|CA-2014-108903|142.488|TEC-AC-10003023|  -3.0|       3|     5|3/10/2014|      Same Day|
+-----------+--------+----------

In [0]:
# Product category and sub category
joined_df = order_df.join(product_df, order_df['Product ID'] == product_df["Product ID"], how = 'left') \
                    .select("Customer ID",
                            "Discount",
                            "Order Date",
                            "Order ID",
                            "Price",
                            order_df["Product ID"],
                            "Profit",
                            "Quantity",
                            "Row ID",
                            "Ship Date",
                            "Ship Mode",
                            "Category",
                            "Sub-Category")
display(joined_df)

Customer ID Discount Order Date Order ID Price Product ID Profit Quantity Row ID Ship Date Ship Mode Category Sub-Category JK-15370 0.3 21/8/2016 CA-2016-122581 573.174 FUR-CH-10002961 63.69 7 1 25/8/2016 Standard Class Furniture Chairs JK-15370 0.3 21/8/2016 CA-2016-122581 573.174 FUR-CH-10002961 63.69 7 1 25/8/2016 Standard Class Furniture Chairs BD-11320 0.0 23/9/2017 CA-2017-117485 291.96 TEC-AC-10004659 102.19 4 2 29/9/2017 Standard Class Technology Accessories LB-16795 0.7 6/10/2016 US-2016-157490 17 OFF-BI-10002824 -14.92 4 3 7/10/2016 First Class Office Supplies Binders KB-16315 0.2 2/7/2015 CA-2015-111703 15.552 OFF-PA-10003349 5.64 3 4 9/7/2015 Standard Class Office Supplies Paper DO-13435 0.2 3/10/2014 CA-2014-108903 142.488 TEC-AC-10003023 -3.0 3 5 3/10/2014 Same Day Technology Accessories CB-12025 0.0 27/11/2016 CA-2016-117583 79.95 OFF-BI-10004233 38.38 5 6 30/11/2016 First Class Office Supplies Binders SM-20005 0.0 10/12/2014 CA-2014-148488 11 OFF-PA-10004470 5.23 2 7 15/12/2014 Standard Class Office Supplies Paper RD-19480 0.0 1/12/2016 CA-2016-136434 17.31 FUR-FU-10001196 5.19 3 8 7/12/2016 Standard Class Furniture Furnishings JM-16195 0.0 30/4/2014 CA-2014-160094 826 OFF-ST-10000585 214.0 5 9 2/5/2014 First Class Office Supplies Storage SC-20230 0.0 3/8/2017 CA-2017-141747 16.06 OFF-ST-10003996 4.18 1 10 8/8/2017 Second Class Office Supplies Storage BO-11350 0.2 3/5/2017 CA-2017-132199 8 OFF-FA-10002280 2.8 2 11 8/5/2017 Standard Class Office Supplies Fasteners BD-11320 0.2 27/11/2017 CA-2017-107125 117.488 OFF-BI-10001989 41.12 7 12 2/12/2017 Standard Class Office Supplies Binders AB-10105 0.7 19/9/2017 CA-2017-153822 18.18 OFF-BI-10001460 -13.94 4 13 25/9/2017 Standard Class Office Supplies Binders NP-18670 0.0 12/10/2017 CA-2017-150091 45 TEC-AC-10002167 4.0 3 14 16/10/2017 Standard Class Technology Accessories KD-16270 0.0 2/9/2016 CA-2016-130407 39.98 FUR-FU-10001967 10.0 2 15 6/9/2016 Standard Class Furniture Furnishings BF-11005 0.6 28/7/2016 US-2016-105452 302 FUR-FU-10003806 -378.4 5 16 1/8/2016 Standard Class Furniture Furnishings LE-16810 0.8 27/5/2014 US-2014-117058 17.46 OFF-BI-10004139 -30.56 6 17 30/5/2014 First Class Office Supplies Binders TT-21070 0.0 13/11/2017 CA-2017-122490 344.91 OFF-ST-10000991 10.35 3 18 18/11/2017 Standard Class Office Supplies Storage CA-12055 0.2 22/11/2016 US-2016-164945 134.272 OFF-BI-10001524 47.0 8 19 27/11/2016 Standard Class Office Supplies Binders GD-14590 0.0 5/5/2014 CA-2014-111934 11.88 OFF-BI-10004364 5.0 2 20 7/5/2014 First Class Office Supplies Binders DK-12895 0.0 8/3/2015 CA-2015-105627 373.08 FUR-FU-10000308 82.08 6 21 12/3/2015 Standard Class Furniture Furnishings RM-19675 0.0 19/11/2014 CA-2014-158274 503.96 TEC-PH-10003273 131.03 4 22 24/11/2014 Second Class Technology Phones MY-18295 0.0 28/4/2014 CA-2014-118976 5.34 OFF-AR-10004752 1.5 2 23 3/5/2014 Standard Class Office Supplies Art DB-13555 0.2 14/9/2017 CA-2017-115882 74.352 OFF-PA-10001125 23.24 3 24 17/9/2017 First Class Office Supplies Paper JS-15880 0.0 21/12/2015 US-2015-126214 1618 FUR-TA-10003748 356.04 13 25 24/12/2015 Second Class Furniture Tables MJ-17740 0.0 11/3/2017 CA-2017-147291 895.92 OFF-BI-10003091 421.08 4 26 17/3/2017 Standard Class Office Supplies Binders JL-15835 0.0 17/12/2015 US-2015-138121 142.36 FUR-CH-10004875 38.44 2 27 17/12/2015 Same Day Furniture Chairs PF-19120 0.8 7/4/2015 CA-2015-140025 463.248 OFF-AP-10002651 -1181.28 8 28 11/4/2015 Standard Class Office Supplies Appliances KB-16315 0.0 26/8/2014 CA-2014-103331 3.38 OFF-PA-10002659 1.55 1 29 1/9/2014 Standard Class Office Supplies Paper DO-13645 0.0 4/12/2017 CA-2017-118003 302.94 FUR-CH-10004860 18.18 3 30 10/12/2017 Standard Class Furniture Chairs PG-18820 0.0 27/7/2015 US-2015-129553 29.97 TEC-PH-10004897 0.3 3 31 2/8/2015 Standard Class Technology Phones AJ-10780 0.0 14/5/2017 US-2017-133361 14 OFF-AR-10003045 6.62 5 32 17/5/2017 First Class Office Supplies Art JG-15115 0.7 3/12/2015 CA-2015-123092 95 OF

In [0]:
yr_prof = joined_df.withColumn("year", substring(joined_df["Order Date"], -4, 4))                         

In [0]:
profit_sales = yr_prof.groupBy('year','Category','Sub-Category','Customer ID') \
                        .agg(sum('Profit').alias('Total_sales')) 
display(profit_sales)

year Category Sub-Category Customer ID Total_sales 2017 Technology Phones HR-14770 20.36 2017 Office Supplies Binders AW-10930 2.17 2016 Office Supplies Art DC-12850 1.63 2017 Office Supplies Binders BP-11290 -463.51 2015 Furniture Chairs SV-20785 142.62 2015 Office Supplies Binders SG-20470 -1.29 2016 Furniture Bookcases HF-14995 37.589999999999996 2017 Office Supplies Appliances SM-20950 68.82 2015 Furniture Furnishings BF-10975 0.74 2014 Office Supplies Paper CR-12625 9.53 2017 Technology Accessories JL-15835 135.53 2015 Office Supplies Art IM-15070 1.63 2017 Office Supplies Storage Dp-13240 98.97 2017 Office Supplies Appliances AT-10435 68.04 2016 Furniture Furnishings DS-13180 19.7 2015 Office Supplies Paper MO-17800 15.55 2015 Furniture Tables MO-17800 -32.52 2017 Office Supplies Paper JF-15565 10.89 2016 Office Supplies Binders SK-19990 3.44 2016 Technology Accessories CM-12235 52.5 2017 Technology Phones PR-18880 37.8 2017 Furniture Furnishings JM-16195 50.11 2016 Office Supplies Binders DV-13465 89.95 2017 Technology Accessories KB-16240 777.68 2016 Technology Phones GT-14710 54.44 2017 Technology Phones EM-13825 55.44 2017 Furniture Furnishings PB-18805 39.98 2017 Office Supplies Labels PG-18895 3.0 2017 Office Supplies Fasteners CJ-12010 5.68 2017 Office Supplies Labels CP-12085 17.76 2014 Office Supplies Fasteners RC-19960 14.53 2014 Technology Copiers CS-11860 90.0 2017 Furniture Furnishings MG-17650 1.74 2015 Office Supplies Labels JM-15265 1.99 2017 Office Supplies Appliances JL-15505 412.47 2016 Technology Phones AY-10555 6.7 2015 Office Supplies Storage MG-18145 -7.27 2016 Office Supplies Paper MT-18070 15.55 2016 Office Supplies Storage SZ-20035 49.32 2016 Office Supplies Art JO-15280 22.76 2017 Furniture Bookcases DS-13180 -36.24 2017 Technology Phones FH-14350 -34.31 2014 Office Supplies Binders DJ-13510 8.26 2017 Office Supplies Binders LW-17125 5.08 2014 Office Supplies Envelopes SB-20170 4.72 2015 Furniture Furnishings JC-15775 3.24 2016 Office Supplies Art JK-15730 15.56 2016 Office Supplies Supplies EH-14125 20.16 2015 Office Supplies Appliances GA-14515 419.82 2016 Office Supplies Paper ZD-21925 5.0 2015 Technology Accessories SS-20515 64.37 2017 Office Supplies Supplies MG-17650 5.89 2017 Office Supplies Appliances SC-20380 120.94 2016 Office Supplies Fasteners BE-11455 1.71 2016 Office Supplies Binders CD-12790 55.94 2017 Office Supplies Paper RR-19525 6.24 2014 Office Supplies Storage JD-16015 -13.64 2016 Office Supplies Binders MP-17965 -29.9 2016 Furniture Furnishings MZ-17515 -9.09 2017 Office Supplies Appliances DB-13555 94.28 2014 Technology Phones LC-16885 200.87 2017 Furniture Furnishings SO-20335 7.24 2016 Office Supplies Binders RH-19555 -20.09 2014 Office Supplies Art VM-21835 6.51 2014 Technology Machines JA-15970 -21.95 2016 Office Supplies Art HW-14935 3.47 2015 Furniture Chairs KD-16615 71.77 2016 Furniture Chairs PO-19180 5.2 2014 Office Supplies Storage CD-12790 13.89 2015 Office Supplies Supplies AH-10690 -4.9 2017 Furniture Furnishings SM-20320 31.59 2016 Furniture Furnishings DK-13375 15.36 2016 Office Supplies Paper JE-15745 27.88 2017 Technology Copiers SV-20365 70.0 2016 Office Supplies Binders IM-15055 2.81 2017 Office Supplies Paper RD-19810 174.17999999999998 2017 Office Supplies Paper EH-13945 18.14 2014 Office Supplies Binders ME-17320 548.98 2016 Furniture Furnishings SV-20935 13.8 2017 Technology Phones CK-12595 15.99 2016 Furniture Furnishings KD-16615 22.38 2014 Office Supplies Storage JD-16150 10.35 2015 Office Supplies Binders SS-20875 -56.08 2017 Furniture Tables EB-13705 -75.83 2014 Furniture Tables DM-13015 -108.33 2017 Office Supplies Binders PC-18745 -0.99 2015 Office Supplies Envelopes MT-17815 2.48 2016 Office Supplies Storage AA-10375 1.47 2014 Technology Accessories KM-16720 98.6 2016 Office Supplies Storage DB-13270 582.23 2016 Furniture Furnishings BF-11170 -1.0899999999999999 2017 Furniture Chairs LC-17050 -15.25 2015 Technology Phones NP-18325 382.88 20

In [0]:
yr_prof.printSchema()

root
 |-- Customer ID: string (nullable = true)
 |-- Discount: double (nullable = true)
 |-- Order Date: string (nullable = true)
 |-- Order ID: string (nullable = true)
 |-- Price: string (nullable = true)
 |-- Product ID: string (nullable = true)
 |-- Profit: double (nullable = true)
 |-- Quantity: long (nullable = true)
 |-- Row ID: long (nullable = true)
 |-- Ship Date: string (nullable = true)
 |-- Ship Mode: string (nullable = true)
 |-- Category: string (nullable = true)
 |-- Sub-Category: string (nullable = true)
 |-- year: string (nullable = true)



In [0]:
# Using SQL output the following aggregates
# Profit by Year
# Profit by Year + Product Category
# Profit by Customer
# Profit by Customer + Year

renamed_df = yr_prof.withColumnRenamed('Customer ID','Customer_ID')
renamed_df.createOrReplaceTempView('Profit_tab')
prof_by_yr = spark.sql("select year,sum(profit) tot_prof from Profit_tab group by year")
prof_by_yr_prd_cat = spark.sql("select year, Category, sum(profit) tot_prof from Profit_tab group by year, Category")
prof_by_cust = spark.sql("select Customer_ID, sum(profit) tot_prof from Profit_tab group by Customer_ID")
prof_by_cust_yr = spark.sql("select Customer_ID,year,sum(profit) tot_prof from Profit_tab group by Customer_ID,year")

display(prof_by_yr)
display(prof_by_yr_prd_cat)
display(prof_by_cust)
display(prof_by_cust_yr)

year tot_prof 2016 68565.92000000013 2017 127664.09999999973 2014 41498.66000000001 2015 66289.61999999994

year Category tot_prof 2016 null 404.44000000000005 2017 null 488.5100000000001 2014 null 523.13 2016 Office Supplies 35973.81000000003 2016 Furniture 7750.2099999999955 2015 Technology 36823.860000000044 2015 Furniture 3392.14 2014 Office Supplies 22663.870000000006 2016 Technology 24437.46000000004 2015 null 583.1600000000001 2015 Office Supplies 25490.45999999999 2017 Technology 78483.19999999998 2014 Furniture -5174.66 2017 Office Supplies 45330.640000000065 2014 Technology 23486.320000000003 2017 Furniture 3361.7499999999995

Customer_ID tot_prof VW-21775 -874.66 RR-19315 -73.83000000000001 PB-19210 21.9 MS-17530 84.02 EM-13960 102.3 MY-17380 331.03 KH-16630 735.4799999999999 BD-11500 1112.51 SW-20275 332.75999999999993 AH-10690 1296.8899999999999 JF-15490 -18.049999999999983 JF-15415 635.6400000000001 PH-18790 47.89 PW-19240 1261.5400000000004 IM-15070 553.8900000000001 KF-16285 1664.29 NW-18400 1028.0700000000002 KM-16225 635.43 OT-18730 -925.5600000000001 JH-15985 -644.4799999999999 KD-16615 539.72 MG-18145 107.51000000000008 SM-20320 -1972.8999999999999 ND-18370 353.24 BG-11695 107.59 BS-11380 -17.529999999999983 PP-18955 1533.89 SO-20335 -19.28000000000003 TB-21400 2821.7099999999996 PJ-18835 442.13999999999993 DN-13690 540.5300000000001 JK-15370 393.54 DG-13300 562.7700000000001 DJ-13420 483.03 CB-12025 -276.4799999999996 MC-17575 210.92000000000002 NB-18655 117.63999999999999 AR-10345 -221.05 BS-11365 2640.41 DS-13030 198.98000000000002 GZ-14545 828.1700000000001 SS-20515 210.98000000000005 LL-16840 560.5100000000001 PO-19180 1276.1100000000001 ND-18460 443.3399999999999 CC-12220 393.97 AB-10105 5483.75 CA-12265 284.58000000000004 JA-15970 -819.8799999999999 CC-12670 186.88 PF-19225 591.29 DB-13360 370.9 CS-12355 1080.68 JK-15325 55.58 TP-21130 1128.65 RE-19405 6.05 DK-12895 925.97 CL-12565 1933.1899999999998 RH-19555 0.3099999999999987 VF-21715 -93.1 ME-17320 2133.46 EM-14065 40.03000000000001 AB-10015 129.68 TC-20980 9010.180000000002 ML-17755 409.99 RS-19870 9.58 BF-11170 1989.8200000000002 RB-19645 72.68 GK-14620 1706.1799999999998 KH-16510 683.5499999999998 NK-18490 121.23 BO-11425 59.46 SH-19975 553.65 KT-16465 258.04999999999995 TS-21340 -165.38 DB-12970 233.41 EH-14005 -84.77000000000004 FH-14365 2057.92 TB-21250 260.3 PM-18940 157.88 CP-12340 -1850.3099999999997 AW-10840 65.78 HM-14980 118.51 CK-12595 527.35 SC-20680 370.16999999999996 KB-16405 273.85999999999996 GT-14755 -6.14 RD-19720 207.72000000000003 SC-20260 670.98 SW-20455 793.6400000000001 JW-15220 2174.0499999999997 MB-17305 213.34000000000003 NM-18445 2751.7 GH-14425 1176.3899999999999 CS-12400 -474.52000000000004 CD-12790 389.44999999999993 NS-18505 40.74000000000004 HK-14890 956.9700000000003 ST-20530 132.18 GM-14695 188.45999999999998 FA-14230 551.33 SV-20815 199.64000000000001 BS-11800 194.05 CC-12550 34.3 PT-19090 -20.05 SC-20845 31.18 LM-17065 -44.879999999999995 NC-18535 1352.0199999999998 BD-11725 334.47 MO-17800 179.98 JE-16165 790.0199999999999 JS-15940 -327.92999999999995 DB-12910 431.38000000000005 AS-10135 23.34 VP-21760 -1018.9100000000001 MK-17905 -405.4299999999999 AS-10045 -253.59000000000003 JM-15580 113.12 SC-20695 611.82 SW-20245 -19.579999999999995 SC-20725 1278.18 JF-15565 1074.0700000000002 BH-11710 791.3600000000001 AS-10090 64.31999999999998 AI-10855 858.7700000000001 RD-19660 835.77 MG-17875 -470.7700000000001 MC-17845 850.9200000000002 BF-11020 311.44 XP-21865 630.6999999999999 BT-11530 519.2099999999999 GZ-14470 1088.1599999999999 RB-19360 6976.36 SM-20905 -16475.55 LD-17005 556.7699999999999 BW-11065 -46.17999999999999 JM-15865 1575.07 SP-20545 -118.38000000000001 MJ-17740 1054.5400000000002 SP-20860 584.43 RB-19330 -164.41 MY-18295 -371.7100000000001 MP-18175 225.48999999999998 KC-16255 846.1399999999999 CS-12130 153.67000000000002 EA-14035 -52.559999999999945 TH-21115 -252.55000000000004 LC-16870 -162.81000000000006 HR-14830 1197.3700000000001 JL-15850 779.9000000000002 BT-11305 417.58000000000004 DB-13120 -1421.78 SV-20935 106.62 TP-21415 -1022.86 JH-15430 -24.05999999999999 BB-10990 50.349999999999994 SC-20230 439.83 BK-11260 -63.29999999999999 TZ-21580 233.93 AH-10210 1308.56 JK-16120 122.66000000000005 MF-17665 -341.53 DO-13645 293.84999999999997 SP-20650 219.03 AG-10765 -8.419999999999995 DK-13090 536.3899999999999 EM-14200 21.83 KN-16390 -151.15000000000003 AJ-10795 1158.71 BW-11110 950.9100000000001 ED-13885 670.4499999999999 LS-17200 243.82000000000002 AS-10240 33.69 CS-12490 -295.88 JO-15550 167.12999999999997 ER-13855 -295.330000000

Customer_ID year tot_prof SC-20380 2017 270.29 CK-12325 2014 326.42 JH-15910 2016 77.6 JF-15355 2015 161.10999999999999 AS-10240 2016 23.18 ED-13885 2016 185.14 BP-11230 2014 27.56 CV-12805 2016 -35.390000000000015 TH-21235 2014 -2.9299999999999997 EH-13945 2015 10.62 DL-13315 2016 233.25 PS-19045 2014 623.2 BM-11575 2016 109.44 ML-17395 2017 11.1 JM-16195 2017 254.88 AS-10225 2016 -6.21 BT-11680 2017 35.43 JH-15820 2017 -19.939999999999998 RS-19870 2017 6.08 CM-12445 2014 10.780000000000001 HG-14965 2016 136.14 TM-21010 2017 205.84000000000003 SF-20065 2017 110.13000000000001 AC-10615 2015 -32.300000000000004 EH-13990 2015 28.380000000000003 DD-13570 2016 -6.9 PN-18775 2015 6.46 SG-20080 2017 218.25 IL-15100 2017 438.68000000000006 LW-17125 2014 21.75 BG-11035 2014 54.19 HP-14815 2014 101.69 SC-20260 2014 96.77 BD-11500 2015 70.98 LO-17170 2015 34.45 KM-16660 2014 3.0 JF-15295 2017 59.940000000000005 BT-11395 2015 194.73000000000002 TS-21505 2016 -69.83 MC-17635 2016 27.42 JK-15625 2017 8.860000000000001 NC-18340 2016 26.29 NG-18430 2014 134.82 AZ-10750 2014 74.73999999999998 AG-10390 2017 8.3 MC-18130 2014 24.98 CV-12295 2016 51.980000000000004 BE-11410 2017 178.70999999999998 AM-10705 2017 392.01 CL-11890 2017 353.07 ES-14020 2017 871.8199999999999 DE-13255 2016 21.59 FH-14275 2014 297.18 LL-16840 2014 110.88 FW-14395 2017 5.81 GW-14605 2017 -451.09000000000003 JO-15280 2016 61.43000000000001 EB-13870 2014 7.02 JK-15730 2014 -212.60999999999999 AB-10015 2014 12.82 SN-20710 2015 91.22 SR-20425 2017 -3391.6600000000008 JM-15250 2016 279.43 SJ-20500 2014 57.93 LC-16930 2017 12.04 RB-19570 2016 -5.979999999999997 EB-13870 2017 -80.44 PG-18895 2014 -70.73 BS-11800 2015 77.11 MG-17890 2014 -4.8 KT-16465 2015 28.81 EL-13735 2017 18.45 KW-16435 2015 1600.8500000000001 RF-19735 2017 391.46999999999997 DS-13180 2016 -55.95 JG-15160 2015 1293.73 JL-15175 2016 -2.0 DL-12925 2015 304.39 LH-17020 2017 -152.86999999999998 SW-20245 2017 -64.07 CD-11920 2015 17.75 MJ-17740 2017 403.71999999999997 TB-21595 2014 6.75 HK-14890 2015 300.07000000000005 JL-15235 2016 103.36000000000001 AD-10180 2017 1866.92 SC-20050 2016 146.65 SC-20725 2016 273.17999999999995 AT-10735 2016 70.35 BB-10990 2017 6.92 EB-13975 2016 151.89 BP-11095 2015 53.56 BS-11755 2014 -330.55 MW-18220 2017 8.49 DM-13015 2015 6.6 PC-18745 2017 -0.99 TC-21475 2015 27.0 CH-12070 2015 57.39 RB-19645 2016 19.33 BT-11485 2015 117.39 PM-19135 2015 426.81000000000006 CB-12025 2016 161.25 AH-10120 2017 382.0 SP-20650 2015 95.84 MZ-17335 2015 136.3 AH-10465 2017 147.87 AC-10450 2015 24.98 DS-13180 2017 -29.56 JF-15190 2017 347.08000000000004 DC-12850 2017 -1128.7499999999998 GB-14575 2016 73.22 GD-14590 2016 -155.3 CP-12340 2017 -17.02 AB-10150 2017 40.0 TC-20980 2016 8764.95 EB-13750 2016 139.80999999999997 NG-18355 2014 219.08 TS-21085 2017 -1.97 MB-17305 2017 65.67 SW-20245 2015 -10.840000000000002 SW-20350 2017 -50.25 PB-19150 2016 38.38 ME-17725 2017 23.16000000000001 MT-17815 2016 432.26 JD-15790 2017 10.280000000000001 CM-12115 2015 8.11 SS-20140 2016 6.55 FW-14395 2015 5.48 VS-21820 2017 -6.42 CP-12085 2014 62.39 NZ-18565 2015 82.82000000000001 RD-19930 2015 39.0 PM-19135 2017 69.6 TC-21535 2016 161.53 TB-21190 2014 161.97 MH-17785 2017 3.35 CB-12415 2017 74.23 ES-14020 2014 15.22 RH-19555 2016 6.34 LA-16780 2017 16.07 AJ-10780 2016 -5.7 SS-20410 2017 58.910000000000004 DB-13615 2017 60.50000000000001 MS-17830 2014 10.92 AR-10540 2016 9.53 PG-18820 2016 612.6800000000001 BS-11755 2016 82.94999999999999 HK-14890 2016 17.03 JE-15715 2015 50.83 SB-20290 2017 -907.0500000000001 AM-10360 2017 -1.5699999999999932 PG-18895 2016 10.71 BP-11290 2016 -65.75 DW-13585 2015 -371.25 CS-12355 2015 536.85 TS-21430 2014 17.139999999999986 AP-10720 2014 54.65 NF-18475 2015 72.89 SC-20575 2014 32.39 RW-19540 2017 1660.85 VT-21700 2015 -257.93 PA-19060 2014 45.84 EH-14125 2016 -75.1 RA-19945 2017 -105.5 EH-14185 2014 26.43 JW-15220 2016 131.25 TM-21010 2014 128.82999999999998 NC-18625 2014 36.66 HA-1